# 38커뮤니케이션에서 공모주 정보 가져오기

In [308]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xlwings as xw
from openpyxl import Workbook

import matplotlib.pyplot as plt
from matplotlib import font_manager, rc
from matplotlib import style

style.use('ggplot')

%matplotlib inline
font_name=font_manager.FontProperties(fname='c:/Windows/Fonts/malgun.ttf').get_name()
rc('font', family=font_name)

plt.rcParams['axes.unicode_minus']=False

#pd.describe_option() 
pd.set_option('display.max_columns', None)
pd.set_option('display.min_rows', 15)

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

#import urllib.request, urllib.parse, urllib.error, json
from pandas import json_normalize

import requests

from bs4 import BeautifulSoup
from html_table_parser import parser_functions as parser

import datetime

In [202]:
def get_gonmo_data_fr_38communication(dataname):
    tempdata=[]
    page=1

    while(1):
        #type => '전체종목', '수요예측일정', '수요예측결과', '공모청약일정', '신규상장종목'
        datatype={'전체종목':['전체종목','http://www.38.co.kr/html/ipo/ipo.htm?o=&key=&' ],
                  '수요예측일정':['수요예측일정','http://www.38.co.kr/html/fund/index.htm?o=r&'],
                  '수요예측결과':['수요예측결과','http://www.38.co.kr/html/fund/index.htm?o=r1&'],
                  '공모청약일정':['공모주 청약일정','http://www.38.co.kr/html/fund/index.htm?o=k&'],
                  '신규상장':['신규상장종목', 'http://www.38.co.kr/html/fund/index.htm?o=nw&'] }
       
        #url = r'http://www.38.co.kr/html/fund/index.htm?o=nw&'
        url=datatype[dataname][1]
        #print(datatype[dataname][1])
        
        request=requests.get(url, {'page': str(page)})

        html=request.text

        soup=BeautifulSoup(html, 'html.parser')
        #soup

        #for parse in soup.find_all('table', {'summary':'신규상장종목'}):
        #    print(parse)


        print(datatype[dataname][0])
        
        if(datatype[dataname][0]=='전체종목'):
            print(1)
            temp=soup.find_all('table',{'border':"0", 'cellpadding':"4", 'cellspacing':"0",'summary':"", 'width':'100%'})
        else:
            print(2)
            temp=soup.find_all('table', {'summary':datatype[dataname][0]})


        temp2=parser.make2d(temp[0])
        #print(temp2)

        tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])
    
        tempdata.rename(columns={'기업명':'종목명', 
                                 '희망공모가(원)':'희망공모가',
                                 '공모가(원)':'확정공모가', 
                                 '공모희망가(원)':'희망공모가',
                                 '공모금액(백만원)':'공모금액(백만)'}, inplace=True)
        tempdata

        if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
            break

        if (page==1):
            all_data=tempdata
        else:
            all_data=pd.concat([all_data, tempdata], ignore_index=True)

        print(all_data)
        page+=1
        all_data=all_data.drop_duplicates()
        
    return     all_data

In [203]:
all_ipo=get_gonmo_data_fr_38communication('전체종목')
all_suyo=get_gonmo_data_fr_38communication('수요예측일정')
all_suyo_rslt=get_gonmo_data_fr_38communication('수요예측결과')
all_gongmo=get_gonmo_data_fr_38communication('공모청약일정')
all_newstk=get_gonmo_data_fr_38communication('신규상장')

전체종목
1
           청구일            종목명  상태    자본금(백만)     매출액(백만) 당기순이익(백만)  \
0   2022/01/25         쓰리디팩토리          1,449      11,435       -96   
1   2022/01/12     미래에셋비전스팩1호             32           0       -14   
2   2022/01/06            샤페론          9,701           0   -26,543   
3   2022/01/05      SK쉴더스(유가)         37,942     305,122    21,833   
4   2022/01/05         쏘카(유가)          2,879     261,824   -67,745   
5   2021/12/23         키움스팩6호             23           0         0   
6   2021/12/23           가온칩스          4,714      17,098     1,852   
7   2021/12/22        에이치피에스피          8,354      61,174    17,658   
8   2021/12/21             핀텔          3,948       4,886       -24   
9   2021/12/21     교보생명보험(유가)        102,500  15,708,927   382,865   
10  2021/12/17         유진스팩8호  승인         92           0         0   
11  2021/12/17         미코세라믹스          2,723      67,615     9,389   
12  2021/12/17          영창케미칼          8,056      60,760     2,506   
13  2021/12/1

전체종목
1
           청구일         종목명  상태 자본금(백만)    매출액(백만) 당기순이익(백만)            주간사  \
0   2022/01/25      쓰리디팩토리       1,449     11,435       -96         NH투자증권   
1   2022/01/12  미래에셋비전스팩1호          32          0       -14         미래에셋증권   
2   2022/01/06         샤페론       9,701          0   -26,543         NH투자증권   
3   2022/01/05   SK쉴더스(유가)      37,942    305,122    21,833    NH투자증권,KB증권   
4   2022/01/05      쏘카(유가)       2,879    261,824   -67,745         미래에셋증권   
5   2021/12/23      키움스팩6호          23          0         0           키움증권   
6   2021/12/23        가온칩스       4,714     17,098     1,852           대신증권   
..         ...         ...  ..     ...        ...       ...            ...   
83  2021/07/12       알비더블유  상장   3,965     37,277     3,719         미래에셋증권   
84  2021/07/12       에스엠상선  승인  33,844  1,032,817   107,583         NH투자증권   
85  2021/07/08        지니너스  상장   5,434      3,794    -9,152           대신증권   
86  2021/07/02         모비젠  철회     575     27,820       9

전체종목
1
            청구일           종목명  상태 자본금(백만)  매출액(백만) 당기순이익(백만)          주간사  \
0    2022/01/25        쓰리디팩토리       1,449   11,435       -96       NH투자증권   
1    2022/01/12    미래에셋비전스팩1호          32        0       -14       미래에셋증권   
2    2022/01/06           샤페론       9,701        0   -26,543       NH투자증권   
3    2022/01/05     SK쉴더스(유가)      37,942  305,122    21,833  NH투자증권,KB증권   
4    2022/01/05        쏘카(유가)       2,879  261,824   -67,745       미래에셋증권   
5    2021/12/23        키움스팩6호          23        0         0         키움증권   
6    2021/12/23          가온칩스       4,714   17,098     1,852         대신증권   
..          ...           ...  ..     ...      ...       ...          ...   
263  2020/05/25       압타머사이언스  상장   4,463      408    -3,853         키움증권   
264  2020/05/22        바이브컴퍼니  상장   2,697   16,298      -777       한국투자증권   
265  2020/05/20            핌스  상장   3,632   37,783     5,544       DB금융투자   
266  2020/05/08         박셀바이오  상장   3,761        0    -1,254       하나

            청구일         종목명  상태 자본금(백만)  매출액(백만) 당기순이익(백만)            주간사  \
0    2022/01/25      쓰리디팩토리       1,449   11,435       -96         NH투자증권   
1    2022/01/12  미래에셋비전스팩1호          32        0       -14         미래에셋증권   
2    2022/01/06         샤페론       9,701        0   -26,543         NH투자증권   
3    2022/01/05   SK쉴더스(유가)      37,942  305,122    21,833    NH투자증권,KB증권   
4    2022/01/05      쏘카(유가)       2,879  261,824   -67,745         미래에셋증권   
5    2021/12/23      키움스팩6호          23        0         0           키움증권   
6    2021/12/23        가온칩스       4,714   17,098     1,852           대신증권   
..          ...         ...  ..     ...      ...       ...            ...   
413  2019/04/05       펌텍코리아  상장     941  151,070    20,776         한국투자증권   
414  2019/04/05     대모엔지니어링  상장   4,162   51,026     3,119         신한금융투자   
415  2019/04/04       에이스토리  상장   4,659   46,446     2,320       엔에이치투자증권   
416  2019/04/01      유진스팩4호  상장     349        0         0         유진투자증권   

전체종목
1
            청구일         종목명  상태 자본금(백만)    매출액(백만) 당기순이익(백만)          주간사  \
0    2022/01/25      쓰리디팩토리       1,449     11,435       -96       NH투자증권   
1    2022/01/12  미래에셋비전스팩1호          32          0       -14       미래에셋증권   
2    2022/01/06         샤페론       9,701          0   -26,543       NH투자증권   
3    2022/01/05   SK쉴더스(유가)      37,942    305,122    21,833  NH투자증권,KB증권   
4    2022/01/05      쏘카(유가)       2,879    261,824   -67,745       미래에셋증권   
5    2021/12/23      키움스팩6호          23          0         0         키움증권   
6    2021/12/23        가온칩스       4,714     17,098     1,852         대신증권   
..          ...         ...  ..     ...        ...       ...          ...   
593  2017/03/27       제일홀딩스  상장   7,071  6,196,498   371,783  신한금융투자,KB증권   
594  2017/03/20       선익시스템  상장   3,000    143,709    23,612         대신증권   
595  2017/03/15        브이원텍  상장   3,683     24,455     7,969       미래에셋대우   
596  2017/03/14          힘스  상장   2,484     50,876     4,951    KB증권,

...

신규상장종목
2
             종목명       신규상장일   현재가(원) 전일비(%)   확정공모가 공모가대비등락률(%)  시초가(원)  \
0            브이씨  2022/02/24        -      %       -          -%       -   
1        한국스팩10호  2022/02/21        -      %       -          -%       -   
2        인카금융서비스  2022/02/16        -      %       -          -%       -   
3    현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%       -   
4          나래나노텍  2022/02/08        -      %  17,500          -%       -   
5            아셈스  2022/02/07        -      %   8,000          -%       -   
6      스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%       -   
..           ...         ...      ...    ...     ...         ...     ...   
813         삼목강업  2013/04/30        -      %   2,600           %   3,440   
814        세호로보트  2013/04/03        -      %   7,800           %  14,000   
815           윈팩  2013/03/07        -      %   4,000           %   4,050   
816          코렌텍  2013/03/05        -      %  16,000           %  15,950   
817

신규상장종목
2
             종목명       신규상장일   현재가(원) 전일비(%)   확정공모가 공모가대비등락률(%) 시초가(원)  \
0            브이씨  2022/02/24        -      %       -          -%      -   
1        한국스팩10호  2022/02/21        -      %       -          -%      -   
2        인카금융서비스  2022/02/16        -      %       -          -%      -   
3    현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%      -   
4          나래나노텍  2022/02/08        -      %  17,500          -%      -   
5            아셈스  2022/02/07        -      %   8,000          -%      -   
6      스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%      -   
..           ...         ...      ...    ...     ...         ...    ...   
933      하이제1호스팩  2010/12/03        -      %   4,000           %  4,060   
934         세우테크  2010/12/01        -      %   5,500           %  6,500   
935   코라오홀딩스(유가)  2010/11/30        -      %   4,800           %  7,300   
936         대구방송  2010/11/29        -      %   7,500           %  7,100   
937         케이티롤

신규상장종목
2
                  종목명       신규상장일   현재가(원) 전일비(%)   확정공모가 공모가대비등락률(%)  시초가(원)  \
0                 브이씨  2022/02/24        -      %       -          -%       -   
1             한국스팩10호  2022/02/21        -      %       -          -%       -   
2             인카금융서비스  2022/02/16        -      %       -          -%       -   
3         현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%       -   
4               나래나노텍  2022/02/08        -      %  17,500          -%       -   
5                 아셈스  2022/02/07        -      %   8,000          -%       -   
6           스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%       -   
...               ...         ...      ...    ...     ...         ...     ...   
1053            동국S&C  2009/08/31        -      %  11,000           %   9,900   
1054           에스앤더블류  2009/08/05        -      %   6,700           %  10,000   
1055              게임빌  2009/07/30        -      %  15,000           %  19,800   
1056             동일

신규상장종목
2
              종목명       신규상장일   현재가(원) 전일비(%)   확정공모가 공모가대비등락률(%)  시초가(원)  \
0             브이씨  2022/02/24        -      %       -          -%       -   
1         한국스팩10호  2022/02/21        -      %       -          -%       -   
2         인카금융서비스  2022/02/16        -      %       -          -%       -   
3     현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%       -   
4           나래나노텍  2022/02/08        -      %  17,500          -%       -   
5             아셈스  2022/02/07        -      %   8,000          -%       -   
6       스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%       -   
...           ...         ...      ...    ...     ...         ...     ...   
1173          빅솔론  2007/08/20        -      %  10,000           %  12,000   
1174       3노드디지탈  2007/08/17        -      %   2,500           %   3,000   
1175     에스엔케이폴리텍  2007/07/30        -      %   8,900           %  12,500   
1176          아구스  2007/07/27        -      %  14,500           %  

신규상장종목
2


In [317]:
#per_capita_1.USD.str.replace(',', '').astype('int64')


all_1=pd.merge(all_ipo, all_suyo, how='left',on=None)
all_2=pd.merge(all_1, all_suyo_rslt, how='left', on=None)
all_3=pd.merge(all_2, all_gongmo, how='left', on=None)
all_4=pd.merge(all_3, all_newstk, how='left', on=None)
all_gongmo_alldata=all_4
all_gongmo_alldata.drop(['예측일','분석'], axis=1, inplace=True)
all_gongmo_alldata['청구일']=pd.to_datetime(all_gongmo_alldata['청구일'])
all_gongmo_alldata['신규상장일']=pd.to_datetime(all_gongmo_alldata['신규상장일'])
#colname=all_gongmo_alldata.columns
colname=['청구일','수요예측일','공모주일정','신규상장일', '종목명','희망공모가','확정공모가', '시초가(원)','시초/공모(%)',  '첫날종가(원)',
         '상태',  '주간사', '주업종',
        '기관경쟁률', '의무보유확약', 
       '청약경쟁률',  '공모금액(백만)', '자본금(백만)', '매출액(백만)', '당기순이익(백만)','현재가(원)', '전일비(%)', '공모가대비등락률(%)', '']

writer = pd.ExcelWriter("C:/Users/gusdyd98gray/OneDrive/현용문서/00.공모주/gongmo_data.xlsx", mode='w',engine='xlsxwriter')

sheetname=str('rawdata_'+datetime.date.today().strftime('%Y_%m_%d'))
all_gongmo_alldata[colname].sort_values(['공모주일정'], axis=0, ascending=False).to_excel(writer, sheet_name = sheetname, encoding='utf-8', index=False)

writer.save()
writer.close()
writer.handles = None



C:\Anaconda3\lib\site-packages\xlsxwriter\workbook.py:336: UserWarning: Calling close() on already closed file.
  warn("Calling close() on already closed file.")


----

----

## PROGRAM END

In [117]:
#38커뮤니케이션 사이트에서 전체종목 페이지의 데이터 가져오기
tempdata=[]
all_gongmo_ipo=[]
page=1


while (1): 
    url = r'http://www.38.co.kr/html/ipo/ipo.htm?o=&key=&'
    request=requests.get(url, {'page':str(page)})

    html=request.text

    soup=BeautifulSoup(html, 'html.parser')
    #soup

    #for parse in soup.find_all('table', 'summary'):
    #    print(parse)

    temp=soup.find_all('table',{'border':"0", 'cellpadding':"4", 'cellspacing':"0",'summary':"", 'width':'100%'})
    #temp


    temp2=parser.make2d(temp[0])
    #print(temp2)

    tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])
    #df_gongmo_allipo


    tempdata.columns
    tempdata.rename(columns={'기업명':'종목명'}, inplace=True)
    tempdata.columns
    
    if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
        break
        
    if (page==1):
        all_gongmo_ipo=tempdata
    else:
        all_gongmo_ipo=pd.concat([all_gongmo_ipo, tempdata], ignore_index=True)
    
    print(tempdata)
    page+=1
    
    

Index(['청구일', '기업명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

Index(['청구일', '종목명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

           청구일            종목명  상태    자본금(백만)     매출액(백만) 당기순이익(백만)  \
0   2022/01/25         쓰리디팩토리          1,449      11,435       -96   
1   2022/01/12     미래에셋비전스팩1호             32           0       -14   
2   2022/01/06            샤페론          9,701           0   -26,543   
3   2022/01/05      SK쉴더스(유가)         37,942     305,122    21,833   
4   2022/01/05         쏘카(유가)          2,879     261,824   -67,745   
5   2021/12/23         키움스팩6호             23           0         0   
6   2021/12/23           가온칩스          4,714      17,098     1,852   
7   2021/12/22        에이치피에스피          8,354      61,174    17,658   
8   2021/12/21             핀텔          3,948       4,886       -24   
9   2021/12/21     교보생명보험(유가)        102,500  15,708,927   382,865   
10  2021/12/17         유진스팩8호  승인         92           0         0   
11  2021/12/17         미코세라믹스          2,723      67,615     9,389   
12  2021/12/17          영창케미칼          8,056      60,760     2,506   
13  2021/12/16      

Index(['청구일', '기업명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

Index(['청구일', '종목명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

...

Index(['청구일', '기업명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

Index(['청구일', '종목명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

           청구일     종목명  상태 자본금(백만)  매출액(백만) 당기순이익(백만)      주간사  \
0   2000/03/02    케이비씨  상장   2,550   11,388       389    메리츠증권   
1   2000/03/02    안국약품  상장   4,000   20,804     1,580     한화증권   
2   2000/02/24    네오위즈  상장     600    8,489     3,432     현대증권   
3   2000/02/24    우리기술  상장   2,450   11,965     1,091     한화증권   
4   2000/02/24   에이엠에스  상장   1,870    9,510       836     한빛증권   
5   2000/02/17    전신전자  상장   1,570    6,014       990     하나증권   
6   2000/02/10    인피트론  상장     760    3,914       311     동양증권   
7   2000/02/10  삼일인포마인  상장   1,050    7,092       741     교보증권   
8   2000/02/01    이오리스  상장   1,680    5,512       787   S.K.증권   
9   2000/02/01  위즈정보기술  상장   1,000   30,680     2,061     동원증권   
10  2000/02/01   피코소프트  상장     600    7,639     1,153     동원증권   
11  2000/02/01     휴먼컴  상장   1,950    8,839       801    대유리젠트   
12  2000/02/01   코웰시스넷  상장     840    2,348       253     대우증권   
13  2000/02/01   파인디지털  상장   3,700   15,793     5,008     LG증권   
14  2000/0

Index(['청구일', '기업명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

Index(['청구일', '종목명', '상태', '자본금(백만)', '매출액(백만)', '당기순이익(백만)', '주간사', '주업종'], dtype='object')

In [146]:
#38커뮤니케이션 사이트에서 수요예측일정 페이지의 데이터 가져오기
tempdata=[]
all_gongmo_suyo_schedule=[]
page=1

while(1):
    url = r'http://www.38.co.kr/html/fund/index.htm?o=r&'

    request=requests.get(url, {'page': str(page)})

    html=request.text

    soup=BeautifulSoup(html, 'html.parser')
    #soup

    #for parse in soup.find_all('table', {'summary':'수요예측일정'}):
    #    print(parse)

    temp=soup.find_all('table', {'summary':'수요예측일정'})



    temp2=parser.make2d(temp[0])
    #print(temp2)

    tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])
    tempdata.rename(columns={'기업명':'종목명'}, inplace=True)
    tempdata

    if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
        break
        
    if (page==1):
        all_gongmo_suyo_schedule=tempdata
    else:
        all_gongmo_suyo_schedule=pd.concat([all_gongmo_suyo_schedule, tempdata], ignore_index=True)
    
    print(all_gongmo_suyo_schedule)
    page+=1


종목명             수요예측일         희망공모가(원)    확정공모가    공모금액(백만)  \
0           보로노이  2022.02.24~02.25    50,000~65,000        -     100,000   
1          모아데이타  2022.02.21~02.22    24,000~28,000        -           -   
2       SK증권스팩7호  2022.02.16~02.17      2,000~2,000        -       6,000   
3           비씨엔씨  2022.02.16~02.17     9,000~11,500        -      22,500   
4             노을  2022.02.15~02.16    13,000~17,000        -      19,500   
5            브이씨  2022.02.10~02.11    15,000~19,500        -      15,000   
6           풍원정밀  2022.02.10~02.11    13,200~15,200        -      39,600   
7       스톤브릿지벤처스  2022.02.09~02.10     9,000~10,500        -      40,500   
8      하나금융스팩21호  2022.02.09~02.10      2,000~2,000        -      12,000   
9           퓨런티어  2022.02.07~02.08    11,400~13,700        -      18,240   
10     IBKS스팩17호  2022.02.03~02.04      2,000~2,000        -       5,000   
11   현대엔지니어링(유가)  2022.01.25~01.26    57,900~75,700        -     926,400   
12       한국스팩10호  2022.01.25~01.26      2,000~2,000        -       9,000   
13      바이오에프디엔씨  2022.01.24~01.25    23,000~29,000        -      29,900   
14       인카금융서비스  2022.01.24~01.25    23,000~27,000        -      20,235   
15         나래나노텍  2022.01.17~01.18    17,500~20,500   17,500      54,250   
16           아셈스  2022.01.17~01.18      7,000~8,000    8,000      14,000   
17     스코넥엔터테인먼트  2022.01.13~01.14     9,000~12,000   13,000      20,036   
18        이지트로닉스  2022.01.13~01.14    19,000~22,000   22,000      37,620   
19  LG에너지솔루션(유가)  2022.01.11~01.12  257,000~300,000  300,000  10,922,500   
20                                                                         

                                            주간사  
0                                 한국투자증권,미래에셋증권  
1                                        하나금융투자  
2                                          SK증권  
3                                        NH투자증권  
4                            한국투자증권㈜한국투자증권,삼성증권  
5                                        한국투자증권  
6                                          대신증권  
7                                     KB증권,삼성증권  
8                                        하나금융투자  
9                                  유안타증권,신한금융투자  
10                                      IBK투자증권  
11  미래에셋증권,KB증권,현대차증권,한국투자증권,NH투자증권,하나금융투자,삼성증권  
12                                       한국투자증권  
13                                       DB금융투자  
14                                       한국투자증권  
15                                       미래에셋증권  
16                                       한국투자증권  
17                                         신영증권  
18                                       NH투자증권  
19         KB증권,대신증권,신한금융,미래에셋증권,신영증권,하나금융,하이투자  
20

             종목명             수요예측일         희망공모가(원)    확정공모가    공모금액(백만)  \
0           보로노이  2022.02.24~02.25    50,000~65,000        -     100,000   
1          모아데이타  2022.02.21~02.22    24,000~28,000        -           -   
2       SK증권스팩7호  2022.02.16~02.17      2,000~2,000        -       6,000   
3           비씨엔씨  2022.02.16~02.17     9,000~11,500        -      22,500   
4             노을  2022.02.15~02.16    13,000~17,000        -      19,500   
5            브이씨  2022.02.10~02.11    15,000~19,500        -      15,000   
6           풍원정밀  2022.02.10~02.11    13,200~15,200        -      39,600   
7       스톤브릿지벤처스  2022.02.09~02.10     9,000~10,500        -      40,500   
8      하나금융스팩21호  2022.02.09~02.10      2,000~2,000        -      12,000   
9           퓨런티어  2022.02.07~02.08    11,400~13,700        -      18,240   
10     IBKS스팩17호  2022.02.03~02.04      2,000~2,000        -       5,000   
11   현대엔지니어링(유가)  2022.01.25~01.26    57,900~75,700        -     926,400   
12       한국스

종목명             수요예측일         희망공모가(원)   확정공모가 공모금액(백만)  \
0          애드바이오텍  2022.01.06~01.07      7,000~8,000   7,000    9,520   
1       디비금융스팩10호  2022.01.06~01.07      2,000~2,000   2,000   10,000   
2            케이옥션  2022.01.06~01.07    17,000~20,000  20,000   27,200   
3             오토앤  2022.01.05~01.06      4,200~4,800   5,300   12,085   
4            래몽래인  2021.12.15~12.16    11,500~13,000  15,000   13,800   
5       하나금융스팩20호  2021.12.13~12.14      2,000~2,000   2,000    6,000   
6         NH스팩22호  2021.12.13~12.14      2,000~2,000   2,000   12,000   
7          하이스팩7호  2021.12.06~12.07      2,000~2,000   2,000   10,000   
8         교보스팩11호  2021.12.06~12.07      2,000~2,000   2,000    8,400   
9        케이티비네트워크  2021.11.29~11.30      5,800~7,200   5,800  116,000   
10             툴젠  2021.11.25~11.26  100,000~120,000  70,000  100,000   
11     대신밸런스스팩11호  2021.11.17~11.18      2,000~2,000   2,000   13,000   
12  신한서부티엔디리츠(유가)  2021.11.17~11.18      5,000~5,000   5,000  134,889   
13  미래에셋글로벌리츠(유가)  2021.11.15~11.17      5,000~5,000   5,000   75,100   
14           마인즈랩  2021.11.08~11.09    26,000~30,000  30,000   15,715   
15          알비더블유  2021.11.05~11.08    18,700~21,400  21,400   23,431   
16          바이옵트로  2021.11.03~11.04      7,500~8,500   7,500    7,500   
17             트윔  2021.11.02~11.03    17,800~20,400  22,000   21,716   
18         지오엘리먼트  2021.10.28~10.29      7,600~8,700  10,000   11,757   
19     NH올원리츠(유가)  2021.10.28~10.29      5,000~5,000   5,000  140,500   
20                                                                      

                                      주간사  
0                                    대신증권  
1                                  DB금융투자  
2                                    신영증권  
3                            미래에셋증권,현대차증권  
4                                 IBK투자증권  
5                                  하나금융투자  
6                                  NH투자증권  
7                                  하이투자증권  
8                                    교보증권  
9   한국투자증권,NH투자증권,삼성증권,유진투자증권,하이투자증권,KB증권  
10                                 한국투자증권  
11                                   대신증권  
12                   한국투자증권,신한금융투자,하나금융투자  
13                     미래에셋증권,KB증권,NH투자증권  
14                          NH투자증권,하나금융투자  
15                                 미래에셋증권  
16                                 한국투자증권  
17                                   대신증권  
18                                 NH투자증권  
19                     한국투자증권,NH투자증권,대신증권  
20

              종목명             수요예측일         희망공모가(원)    확정공모가    공모금액(백만)  \
0            보로노이  2022.02.24~02.25    50,000~65,000        -     100,000   
1           모아데이타  2022.02.21~02.22    24,000~28,000        -           -   
2        SK증권스팩7호  2022.02.16~02.17      2,000~2,000        -       6,000   
3            비씨엔씨  2022.02.16~02.17     9,000~11,500        -      22,500   
4              노을  2022.02.15~02.16    13,000~17,000        -      19,500   
5             브이씨  2022.02.10~02.11    15,000~19,500        -      15,000   
6            풍원정밀  2022.02.10~02.11    13,200~15,200        -      39,600   
7        스톤브릿지벤처스  2022.02.09~02.10     9,000~10,500        -      40,500   
8       하나금융스팩21호  2022.02.09~02.10      2,000~2,000        -      12,000   
9            퓨런티어  2022.02.07~02.08    11,400~13,700        -      18,240   
10      IBKS스팩17호  2022.02.03~02.04      2,000~2,000        -       5,000   
11    현대엔지니어링(유가)  2022.01.25~01.26    57,900~75,700        -     926,400   

종목명             수요예측일       희망공모가(원)   확정공모가   공모금액(백만)  \
0         비트나인  2021.10.25~10.26    8,700~9,700  11,000     18,017   
1          디어유  2021.10.25~10.26  18,000~24,000  26,000     59,400   
2       아이티아이즈  2021.10.25~10.26  12,500~14,300  14,300     22,212   
3         지니너스  2021.10.21~10.22  24,700~32,200  20,000     49,400   
4    카카오페이(유가)  2021.10.20~10.21  60,000~90,000  90,000  1,020,000   
5         피코그램  2021.10.19~10.20  11,000~12,500  12,500     11,000   
6           엔켐  2021.10.15~10.18  30,000~35,000  42,000     67,878   
7          리파인  2021.10.14~10.15  21,000~24,000  21,000     90,930   
8   지앤비에스엔지니어링  2021.10.14~10.15  14,300~17,400  17,400     20,377   
9     아이패밀리에스씨  2021.10.12~10.13  39,000~48,000  25,000     38,142   
10      차백신연구소  2021.10.05~10.06  11,000~15,000  11,000     43,450   
11        지아이텍  2021.10.05~10.06  11,500~13,100  14,000     31,050   
12     NH스팩21호  2021.09.28~09.29    2,000~2,000   2,000     12,500   
13        씨유테크  2021.09.23~09.24    5,100~5,600   6,000     26,775   
14        아스플로  2021.09.16~09.17  19,000~22,000  25,000     11,970   
15          원준  2021.09.15~09.16  52,000~60,000  65,000     52,249   
16   하나금융스팩19호  2021.09.15~09.16    2,000~2,000   2,000     11,000   
17     NH스팩20호  2021.09.14~09.15    2,000~2,000   2,000     40,000   
18     케이카(유가)  2021.09.13~09.28  34,300~43,200  25,000    577,278   
19        실리콘투  2021.09.09~09.10  23,800~27,200  27,200     39,365   
20                                                                   

                        주간사  
0                    하나금융투자  
1                    한국투자증권  
2                    신한금융투자  
3               대신증권,NH투자증권  
4   삼성증권,대신증권,한국투자증권,신한금융투자  
5                   IBK투자증권  
6               대신증권,신한금융투자  
7                      KB증권  
8                      삼성증권  
9                      삼성증권  
10                     삼성증권  
11                   미래에셋증권  
12                   NH투자증권  
13                     대신증권  
14                   미래에셋증권  
15                   NH투자증권  
16                   하나금융투자  
17                   NH투자증권  
18  NH투자증권,대신증권,삼성증권,하나금융투자  
19              삼성증권,미래에셋증권  
20

...

종목명         수요예측일       희망공모가(원)       확정공모가 공모금액(백만)      주간사
0           디이엔티  2005.01.10~-    4,200~5,000   4,000(확정)    7,114     대우증권
1         인터넷엠비씨  2005.01.06~-    4,000~4,800   3,400(확정)   10,200     미래에셋
2   에스엔유프리시젼(유가)  2005.01.04~-  25,000~29,000  27,000(확정)   18,900     동원증권
3          인프라밸리  2004.12.28~-  10,000~12,000   8,400(확정)   12,820     교보증권
4         비아이이엠티  2004.12.23~-    3,700~4,500   3,000(확정)    4,560     대신증권
5            손오공  2004.12.17~-   9,000~11,000       9,300   13,032     한양증권
6         아이크래프트  2004.12.15~-    6,500~8,000       6,000    5,438   미래에셋증권
7          메가스터디  2004.11.30~-  19,000~23,000  18,500(확정)   25,722  굿모닝신한증권
8         대주전자재료  2004.11.25~-    3,200~4,000       3,000    5,264     한투증권
9           텔레칩스  2004.11.25~-    5,000~6,000       4,700    8,089     대우증권
10         모빌리언스  2004.11.24~-    6,500~8,500       4,700    7,800     교보증권
11     넥스트인스트루먼트  2004.11.23~-    3,200~4,100       2,800    6,480     교보증권
12        화인에이티씨  2004.11.15~-    2,800~3,200   2,800(예정)    3,052   LG투자증권
13           유니드  2004.11.10~-  14,200~17,400  14,200(예정)   28,052     삼성증권
14       토비스(유가)  2004.11.03~-    2,600~3,300   2,200(확정)    4,940    브릿지증권
15         신지소프트  2004.10.12~-   9,000~12,000   9,000(확정)    6,300   미래에셋증권
16          태양기전  2004.10.12~-  16,000~21,000  14,000(확정)   21,984     교보증권
17       디지탈디바이스  2004.10.12~-    3,500~4,500   3,100(확정)    3,500     우리증권
18           모코코  2004.10.12~-    3,000~3,800   2,500(확정)    3,990     동원증권
19         케이이엔지  2004.10.07~-    3,000~4,000   2,700(확정)    7,829     동양증권
20

           종목명             수요예측일       희망공모가(원)       확정공모가 공모금액(백만)  \
0         보로노이  2022.02.24~02.25  50,000~65,000           -  100,000   
1        모아데이타  2022.02.21~02.22  24,000~28,000           -        -   
2     SK증권스팩7호  2022.02.16~02.17    2,000~2,000           -    6,000   
3         비씨엔씨  2022.02.16~02.17   9,000~11,500           -   22,500   
4           노을  2022.02.15~02.16  13,000~17,000           -   19,500   
5          브이씨  2022.02.10~02.11  15,000~19,500           -   15,000   
6         풍원정밀  2022.02.10~02.11  13,200~15,200           -   39,600   
...        ...               ...            ...         ...      ...   
1400   토비스(유가)      2004.11.03~-    2,600~3,300   2,200(확정)    4,940   
1401     신지소프트      2004.10.12~-   9,000~12,000   9,000(확정)    6,300   
1402      태양기전      2004.10.12~-  16,000~21,000  14,000(확정)   21,984   
1403   디지탈디바이스      2004.10.12~-    3,500~4,500   3,100(확정)    3,500   
1404       모코코      2004.10.12~-    3,000~3,800   2,500(확정)    3

종목명         수요예측일       희망공모가(원)       확정공모가 공모금액(백만)  \
0           국일제지  2004.10.06~-              -  15,000(확정)    6,000   
1           디엠에스  2004.09.06~-              -  28,400(확정)   36,920   
2           아이레보           -~-    5,000~6,500   6,300(확정)   10,500   
3            레인콤           -~-  37,000~47,000  47,000(확정)   48,840   
4            비트윈           -~-    3,500~4,500   4,000(확정)    4,690   
5       텔코웨어(유가)           -~-  12,000~15,500  12,000(확정)   33,357   
6             다날           -~-  10,000~12,000   8,500(확정)   18,400   
7        한국경제티브이           -~-  10,600~13,000  10,600(확정)    5,151   
8         신성델타테크           -~-    1,700~2,200   1,700(확정)    3,298   
9   LG필립스엘시디(유가)           -~-  37,100~52,600  34,500(확정)  356,160   
10     동아에스텍(유가)           -~-    1,800~2,100   1,800(예정)    5,616   
11     유니퀘스트(유가)           -~-    5,500~6,500   4,000(확정)   19,800   
12          코아로직           -~-  28,000~32,000  23,000(확정)   26,450   
13          한서제약           -~-              -   1,400(확정)        -   
14           테스텍           -~-              -       1,260        -   
15  글로벌에스엠테크리미티드           -~-    2,800~3,200       3,200        -   
16         케이탑리츠           -~-              -       5,500   16,500   
17    모두투어리츠(유가)           -~-    6,000~6,000       6,000   14,100   
18    신한알파리츠(유가)           -~-    5,000~5,000       5,000  114,000   
19    대신밸런스스팩10호           -~-    2,000~2,000       2,000   10,000   
20                                                                   

             주간사  
0           현대증권  
1           한화증권  
2           교보증권  
3           현대증권  
4           미래에셋  
5           삼성증권  
6           LG증권  
7           삼성증권  
8           하나증권  
9           동원증권  
10          동원증권  
11          LG증권  
12        미래에셋증권  
13                
14          대우증권  
15        미래에셋증권  
16        한국투자증권  
17  교보증권,케이비투자증권  
18        신한금융투자  
19          대신증권  
20

               종목명             수요예측일       희망공모가(원)  확정공모가 공모금액(백만)  \
0             보로노이  2022.02.24~02.25  50,000~65,000      -  100,000   
1            모아데이타  2022.02.21~02.22  24,000~28,000      -        -   
2         SK증권스팩7호  2022.02.16~02.17    2,000~2,000      -    6,000   
3             비씨엔씨  2022.02.16~02.17   9,000~11,500      -   22,500   
4               노을  2022.02.15~02.16  13,000~17,000      -   19,500   
5              브이씨  2022.02.10~02.11  15,000~19,500      -   15,000   
6             풍원정밀  2022.02.10~02.11  13,200~15,200      -   39,600   
...            ...               ...            ...    ...      ...   
1421           테스텍               -~-              -  1,260        -   
1422  글로벌에스엠테크리미티드               -~-    2,800~3,200  3,200        -   
1423         케이탑리츠               -~-              -  5,500   16,500   
1424    모두투어리츠(유가)               -~-    6,000~6,000  6,000   14,100   
1425    신한알파리츠(유가)               -~-    5,000~5,000  5,000  114,000   
1426  

종목명 수요예측일 희망공모가(원) 확정공모가 공모금액(백만) 주간사
0

In [147]:
#38커뮤니케이션 사이트에서 수요예측결과 페이지의 데이터 가져오기
tempdata=[]
all_gongmo_suyo_result=[]
page=1

while(1):

    url = r'http://www.38.co.kr/html/fund/index.htm?o=r1&'

    request=requests.get(url, {'page':str(page)})

    html=request.text

    soup=BeautifulSoup(html, 'html.parser')
    #soup

    #for parse in soup.find_all('table', {'summary':'수요예측결과'}):
    #    print(parse)

    temp=soup.find_all('table', {'summary':'수요예측결과'})



    temp2=parser.make2d(temp[0])
    #print(temp2)

    tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])
    tempdata.rename(columns={'기업명':'종목명'}, inplace=True)
    tempdata

    if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
        break
        
    if (page==1):
        all_gongmo_suyo_result=tempdata
    else:
        all_gongmo_suyo_result=pd.concat([all_gongmo_suyo_result, tempdata], ignore_index=True)
    
    print(all_gongmo_suyo_result)
    page+=1

종목명         예측일         공모희망가(원)   공모가(원)   공모금액(백만원)  \
0           나래나노텍  2022.01.17    17,500~20,500   17,500      54,250   
1             아셈스  2022.01.17      7,000~8,000    8,000      14,000   
2       스코넥엔터테인먼트  2022.01.13     9,000~12,000   13,000      20,036   
3          이지트로닉스  2022.01.13    19,000~22,000   22,000      37,620   
4    LG에너지솔루션(유가)  2022.01.11  257,000~300,000  300,000  10,922,500   
5          애드바이오텍  2022.01.06      7,000~8,000    7,000       9,520   
6       디비금융스팩10호  2022.01.06      2,000~2,000    2,000      10,000   
7            케이옥션  2022.01.06    17,000~20,000   20,000      27,200   
8             오토앤  2022.01.05      4,200~4,800    5,300      12,085   
9            래몽래인  2021.12.15    11,500~13,000   15,000      13,800   
10      하나금융스팩20호  2021.12.13      2,000~2,000    2,000       6,000   
11        NH스팩22호  2021.12.13      2,000~2,000    2,000      12,000   
12         하이스팩7호  2021.12.06      2,000~2,000    2,000      10,000   
13        교보스팩11호  2021.12.06      2,000~2,000    2,000       8,400   
14       케이티비네트워크  2021.11.29      5,800~7,200    5,800     116,000   
15             툴젠  2021.11.25  100,000~120,000   70,000     100,000   
16     대신밸런스스팩11호  2021.11.17      2,000~2,000    2,000      13,000   
17  신한서부티엔디리츠(유가)  2021.11.17      5,000~5,000    5,000     134,889   
18  미래에셋글로벌리츠(유가)  2021.11.15      5,000~5,000    5,000      75,100   
19           마인즈랩  2021.11.08    26,000~30,000   30,000      15,715   

        기관경쟁률  의무보유확약                                    주간사  
0       102:1   0.97%                                 미래에셋증권  
1   1618.26:1   7.71%                                 한국투자증권  
2   1724.66:1  59.95%                                   신영증권  
3   1343.51:1   2.94%                                 NH투자증권  
4   2023.37:1  77.38%   KB증권,대신증권,신한금융,미래에셋증권,신영증권,하나금융,하이투자  
5    102.15:1       -                                   대신증권  
6                   -                                 DB금융투자  
7   1638.36:1  36.80%                                   신영증권  
8      1713:1   8.34%                           미래에셋증권,현대차증권  
9   1545.68:1  17.75%                                IBK투자증권  
10                  -                                 하나금융투자  
11                  -                                 NH투자증권  
12                  -                                 하이투자증권  
13                  -                                   교보증권  
14    50.19:1   6.94%  한국투자증권,NH투자증권,삼성증권,유진투자증권,하이투자증권,KB증권  
15    29.54:1   0.10%                                 한국투자증권  
16                  -                                   대신증권  
17   564.84:1  15.28%                   한국투자증권,신한금융투자,하나금융투자  
18  1019.58:1  17.34%                     미래에셋증권,KB증권,NH투자증권  
19   197.55:1  19.74%                          NH투자증권,하나금융투자

              종목명         예측일         공모희망가(원)   공모가(원)   공모금액(백만원)  \
0           나래나노텍  2022.01.17    17,500~20,500   17,500      54,250   
1             아셈스  2022.01.17      7,000~8,000    8,000      14,000   
2       스코넥엔터테인먼트  2022.01.13     9,000~12,000   13,000      20,036   
3          이지트로닉스  2022.01.13    19,000~22,000   22,000      37,620   
4    LG에너지솔루션(유가)  2022.01.11  257,000~300,000  300,000  10,922,500   
5          애드바이오텍  2022.01.06      7,000~8,000    7,000       9,520   
6       디비금융스팩10호  2022.01.06      2,000~2,000    2,000      10,000   
7            케이옥션  2022.01.06    17,000~20,000   20,000      27,200   
8             오토앤  2022.01.05      4,200~4,800    5,300      12,085   
9            래몽래인  2021.12.15    11,500~13,000   15,000      13,800   
10      하나금융스팩20호  2021.12.13      2,000~2,000    2,000       6,000   
11        NH스팩22호  2021.12.13      2,000~2,000    2,000      12,000   
12         하이스팩7호  2021.12.06      2,000~2,000    2,000      10,000   
13    

종목명         예측일       공모희망가(원)  공모가(원)  공모금액(백만원)       기관경쟁률  \
0        알비더블유  2021.11.05  18,700~21,400  21,400     23,431  1719.61 :1   
1        바이옵트로  2021.11.03    7,500~8,500   7,500      7,500    205.12:1   
2           트윔  2021.11.02  17,800~20,400  22,000     21,716  1627.34:1:   
3       지오엘리먼트  2021.10.28    7,600~8,700  10,000     11,757  1613.84 :1   
4   NH올원리츠(유가)  2021.10.28    5,000~5,000   5,000    140,500     628.2:1   
5         비트나인  2021.10.25    8,700~9,700  11,000     18,017   1662.29:1   
6          디어유  2021.10.25  18,000~24,000  26,000     59,400   2001.11:1   
7       아이티아이즈  2021.10.25  12,500~14,300  14,300     22,212   1601.14:1   
8         지니너스  2021.10.21  24,700~32,200  20,000     49,400     66.03:1   
9    카카오페이(유가)  2021.10.20  60,000~90,000  90,000  1,020,000   1714.47:1   
10        피코그램  2021.10.19  11,000~12,500  12,500     11,000   1472.19:1   
11          엔켐  2021.10.15  30,000~35,000  42,000     67,878  1647.40 :1   
12         리파인  2021.10.14  21,000~24,000  21,000     90,930     64.19:1   
13  지앤비에스엔지니어링  2021.10.14  14,300~17,400  17,400     20,377   1134.34:1   
14    아이패밀리에스씨  2021.10.12  39,000~48,000  25,000     38,142     63.10:1   
15      차백신연구소  2021.10.05  11,000~15,000  11,000     43,450    206.23:1   
16        지아이텍  2021.10.05  11,500~13,100  14,000     31,050  2068.17 :1   
17     NH스팩21호  2021.09.28    2,000~2,000   2,000     12,500               
18        씨유테크  2021.09.23    5,100~5,600   6,000     26,775   1565.03:1   
19        아스플로  2021.09.16  19,000~22,000  25,000     11,970    2142.7:1   

    의무보유확약                      주간사  
0   15.98%                   미래에셋증권  
1    0.98%                   한국투자증권  
2    9.20%                     대신증권  
3   15.23%                   NH투자증권  
4   17.07%       한국투자증권,NH투자증권,대신증권  
5    5.96%                   하나금융투자  
6   37.46%                   한국투자증권  
7    9.11%                   신한금융투자  
8    0.10%              대신증권,NH투자증권  
9   70.44%  삼성증권,대신증권,한국투자증권,신한금융투자  
10  12.96%                  IBK투자증권  
11  64.45%              대신증권,신한금융투자  
12   3.22%                     KB증권  
13   4.37%                     삼성증권  
14       -                     삼성증권  
15   1.93%                     삼성증권  
16  25.28%                   미래에셋증권  
17       -                   NH투자증권  
18  22.76%                     대신증권  
19  12.10%                   미래에셋증권

              종목명         예측일         공모희망가(원)   공모가(원)   공모금액(백만원)  \
0           나래나노텍  2022.01.17    17,500~20,500   17,500      54,250   
1             아셈스  2022.01.17      7,000~8,000    8,000      14,000   
2       스코넥엔터테인먼트  2022.01.13     9,000~12,000   13,000      20,036   
3          이지트로닉스  2022.01.13    19,000~22,000   22,000      37,620   
4    LG에너지솔루션(유가)  2022.01.11  257,000~300,000  300,000  10,922,500   
5          애드바이오텍  2022.01.06      7,000~8,000    7,000       9,520   
6       디비금융스팩10호  2022.01.06      2,000~2,000    2,000      10,000   
7            케이옥션  2022.01.06    17,000~20,000   20,000      27,200   
8             오토앤  2022.01.05      4,200~4,800    5,300      12,085   
9            래몽래인  2021.12.15    11,500~13,000   15,000      13,800   
10      하나금융스팩20호  2021.12.13      2,000~2,000    2,000       6,000   
11        NH스팩22호  2021.12.13      2,000~2,000    2,000      12,000   
12         하이스팩7호  2021.12.06      2,000~2,000    2,000      10,000   
13    

종목명         예측일       공모희망가(원)  공모가(원) 공모금액(백만원)      기관경쟁률  \
0            원준  2021.09.15  52,000~60,000  65,000    52,249  1464.10:1   
1     하나금융스팩19호  2021.09.15    2,000~2,000   2,000    11,000              
2       NH스팩20호  2021.09.14    2,000~2,000   2,000    40,000              
3       케이카(유가)  2021.09.13  34,300~43,200  25,000   577,278       40:1   
4          실리콘투  2021.09.09  23,800~27,200  27,200    39,365  1437.63:1   
5         프롬바이오  2021.09.09  21,500~24,500  18,000    64,500    85.71:1   
6        신한스팩8호  2021.09.08    2,000~2,000   2,000    12,500              
7        바이오플러스  2021.09.08  28,500~31,500  31,500    39,900   1220.2:1   
8          에스앤디  2021.09.07  30,000~32,000  28,000    30,690   173.11:1   
9     현대중공업(유가)  2021.09.02  52,000~60,000  60,000   936,000  1835.87:1   
10       유진스팩7호  2021.08.26    2,000~2,000   2,000     8,000              
11         와이엠텍  2021.08.25  21,000~25,000  28,000    12,600  1696.19:1   
12         에이비온  2021.08.24  14,500~17,000  17,000    33,060   139.36:1   
13     SK리츠(유가)  2021.08.23    5,000~5,000   5,000   232,551              
14  일진하이솔루스(유가)  2021.08.19  25,700~34,300  34,300   279,975  1471.01:1   
15    IBKS스팩16호  2021.08.19    2,000~2,000   2,000       100              
16         바이젠셀  2021.08.06  42,800~52,700  52,700    80,741  1271.21:1   
17      브레인즈컴퍼니  2021.08.03  20,000~22,500  25,000    12,000   1428.8:1   
18     롯데렌탈(유가)  2021.08.03  47,000~59,000  59,000   677,834   217.63:1   
19         딥노이드  2021.08.02  31,500~42,000  42,000     9,450  1179.07:1   

    의무보유확약                                            주간사  
0   44.30%                                         NH투자증권  
1        -                                         하나금융투자  
2        -                                         NH투자증권  
3        -                        NH투자증권,대신증권,삼성증권,하나금융투자  
4    8.37%                                    삼성증권,미래에셋증권  
5    1.45%                                         NH투자증권  
6        -                                         신한금융투자  
7    7.80%                                           키움증권  
8    0.01%                                         유진투자증권  
9   53.09%        미래에셋,한국투자,하나금융,KB증권,삼성증권,대신증권,DB금융,신영증권  
10       -                                           유진증권  
11  31.59%                                           KB증권  
12   4.30%                           미래에셋증권,한화투자증권,유진투자증권  
13       -                        한국투자증권,삼성증권,SK증권,하나금융투자  
14  61.52%                         미래에셋증권,삼성증권,현대차증권,대신증권  
15       -                                        IBK투자증권  
16  13.61%                                      대신증권,KB증권  
17   8.92%                                           키움증권  
18  14.65%  NH투자증권,한국투자증권,KB증권,미래에셋증권,삼성증권,신한금융,키움증권,하나금융  
19   7.29%                                           KB증권

...

종목명         예측일       공모희망가(원)      공모가(원) 공모금액(백만원) 기관경쟁률  \
0        디지탈디바이스  2004.10.12    3,500~4,500   3,100(확정)     3,500         
1            모코코  2004.10.12    3,000~3,800   2,500(확정)     3,990         
2          케이이엔지  2004.10.07    3,000~4,000   2,700(확정)     7,829         
3           국일제지  2004.10.06              -  15,000(확정)     6,000         
4           디엠에스  2004.09.06              -  28,400(확정)    36,920         
5           아이레보           -    5,000~6,500   6,300(확정)    10,500         
6            레인콤           -  37,000~47,000  47,000(확정)    48,840         
7            비트윈           -    3,500~4,500   4,000(확정)     4,690         
8       텔코웨어(유가)           -  12,000~15,500  12,000(확정)    33,357         
9             다날           -  10,000~12,000   8,500(확정)    18,400         
10       한국경제티브이           -  10,600~13,000  10,600(확정)     5,151         
11        신성델타테크           -    1,700~2,200   1,700(확정)     3,298         
12  LG필립스엘시디(유가)           -  37,100~52,600  34,500(확정)   356,160         
13     동아에스텍(유가)           -    1,800~2,100   1,800(예정)     5,616         
14     유니퀘스트(유가)           -    5,500~6,500   4,000(확정)    19,800         
15          코아로직           -  28,000~32,000  23,000(확정)    26,450         
16          한서제약           -              -   1,400(확정)         -         
17           테스텍           -              -       1,260         -         
18  글로벌에스엠테크리미티드           -    2,800~3,200       3,200         -         
19         케이탑리츠           -              -       5,500    16,500         

   의무보유확약     주간사  
0       -    우리증권  
1       -    동원증권  
2       -    동양증권  
3       -    현대증권  
4       -    한화증권  
5       -    교보증권  
6       -    현대증권  
7       -    미래에셋  
8       -    삼성증권  
9       -    LG증권  
10      -    삼성증권  
11      -    하나증권  
12      -    동원증권  
13      -    동원증권  
14      -    LG증권  
15      -  미래에셋증권  
16      -          
17      -    대우증권  
18      -  미래에셋증권  
19      -  한국투자증권

               종목명         예측일         공모희망가(원)      공모가(원)   공모금액(백만원)  \
0            나래나노텍  2022.01.17    17,500~20,500      17,500      54,250   
1              아셈스  2022.01.17      7,000~8,000       8,000      14,000   
2        스코넥엔터테인먼트  2022.01.13     9,000~12,000      13,000      20,036   
3           이지트로닉스  2022.01.13    19,000~22,000      22,000      37,620   
4     LG에너지솔루션(유가)  2022.01.11  257,000~300,000     300,000  10,922,500   
5           애드바이오텍  2022.01.06      7,000~8,000       7,000       9,520   
6        디비금융스팩10호  2022.01.06      2,000~2,000       2,000      10,000   
...            ...         ...              ...         ...         ...   
1333     동아에스텍(유가)           -      1,800~2,100   1,800(예정)       5,616   
1334     유니퀘스트(유가)           -      5,500~6,500   4,000(확정)      19,800   
1335          코아로직           -    28,000~32,000  23,000(확정)      26,450   
1336          한서제약           -                -   1,400(확정)           -   
1337           테스텍       

종목명 예측일     공모희망가(원) 공모가(원) 공모금액(백만원) 기관경쟁률 의무보유확약           주간사
0  모두투어리츠(유가)   -  6,000~6,000  6,000    14,100            -  교보증권,케이비투자증권
1  신한알파리츠(유가)   -  5,000~5,000  5,000   114,000            -        신한금융투자
2  대신밸런스스팩10호   -  2,000~2,000  2,000    10,000            -          대신증권

               종목명         예측일         공모희망가(원)     공모가(원)   공모금액(백만원)  \
0            나래나노텍  2022.01.17    17,500~20,500     17,500      54,250   
1              아셈스  2022.01.17      7,000~8,000      8,000      14,000   
2        스코넥엔터테인먼트  2022.01.13     9,000~12,000     13,000      20,036   
3           이지트로닉스  2022.01.13    19,000~22,000     22,000      37,620   
4     LG에너지솔루션(유가)  2022.01.11  257,000~300,000    300,000  10,922,500   
5           애드바이오텍  2022.01.06      7,000~8,000      7,000       9,520   
6        디비금융스팩10호  2022.01.06      2,000~2,000      2,000      10,000   
...            ...         ...              ...        ...         ...   
1336          한서제약           -                -  1,400(확정)           -   
1337           테스텍           -                -      1,260           -   
1338  글로벌에스엠테크리미티드           -      2,800~3,200      3,200           -   
1339         케이탑리츠           -                -      5,500      16,500   
1340    모두투어리츠(유가)           -      6,

Empty DataFrame
Columns: [종목명, 예측일, 공모희망가(원), 공모가(원), 공모금액(백만원), 기관경쟁률, 의무보유확약, 주간사]
Index: []

In [149]:
#38커뮤니케이션에서 공모주 청약일정 페이지에서 공모주 청약일정 데이터 크롤링하기
tempdata=[]
all_gongmo=[]
page=1

while(1):
    url = r'http://www.38.co.kr/html/fund/index.htm?o=k&'

    request=requests.get(url, {'page': str(page)})

    html=request.text

    soup=BeautifulSoup(html, 'html.parser')
    #soup

    #for parse in soup.find_all('table', {'summary':'공모주 청약일정'}):
    #    print(parse)

    temp=soup.find_all('table', {'summary':'공모주 청약일정'})



    temp2=parser.make2d(temp[0])
    #print(temp2)

    tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])
    tempdata.rename(columns={'기업명':'종목명'}, inplace=True)
    tempdata

    if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
        break
        
    if (page==1):
        all_gongmo=tempdata
    else:
        all_gongmo=pd.concat([all_gongmo, tempdata], ignore_index=True)
    
    print(all_gongmo)
    page+=1

종목명             공모주일정    확정공모가            희망공모가      청약경쟁률  \
0           보로노이  2022.03.07~03.08        -    50,000~65,000              
1          모아데이타  2022.02.25~02.26        -    24,000~28,000              
2       SK증권스팩7호  2022.02.22~02.23        -      2,000~2,000              
3             노을  2022.02.21~02.22        -    13,000~17,000              
4           비씨엔씨  2022.02.21~02.22        -     9,000~11,500              
5           풍원정밀  2022.02.17~02.18        -    13,200~15,200              
6            브이씨  2022.02.15~02.16        -    15,000~19,500              
7       스톤브릿지벤처스  2022.02.15~02.16        -     9,000~10,500              
8      하나금융스팩21호  2022.02.15~02.16        -      2,000~2,000              
9           퓨런티어  2022.02.14~02.15        -    11,400~13,700              
10       한국스팩10호  2022.02.10~02.11        -      2,000~2,000              
11      바이오에프디엔씨  2022.02.09~02.10        -    23,000~29,000              
12     IBKS스팩17호  2022.02.08~02.09        -      2,000~2,000              
13       인카금융서비스  2022.02.07~02.08        -    23,000~27,000              
14   현대엔지니어링(유가)  2022.02.03~02.04        -    57,900~75,700              
15         나래나노텍  2022.01.24~01.25   17,500    17,500~20,500    24.36:1   
16           아셈스  2022.01.24~01.25    8,000      7,000~8,000  2435.07:1   
17     스코넥엔터테인먼트  2022.01.20~01.21   13,000     9,000~12,000  1751.25:1   
18        이지트로닉스  2022.01.20~01.21   22,000    19,000~22,000   887.40:1   
19  LG에너지솔루션(유가)  2022.01.18~01.19  300,000  257,000~300,000    69.34:1   
20        애드바이오텍  2022.01.13~01.14    7,000      7,000~8,000    27.20:1   
21          케이옥션  2022.01.12~01.13   20,000    17,000~20,000  1408.33:1   
22           오토앤  2022.01.11~01.12    5,300      4,200~4,800  2395.63:1   
23     디비금융스팩10호  2022.01.10~01.11    2,000      2,000~2,000   234.95:1   
24          래몽래인  2021.12.20~12.21   15,000    11,500~13,000  2054.63:1   

                                            주간사 분석  
0                                 한국투자증권,미래에셋증권     
1                                        하나금융투자     
2                                          SK증권     
3                            한국투자증권㈜한국투자증권,삼성증권     
4                                        NH투자증권     
5                                          대신증권     
6                                        한국투자증권     
7                                     KB증권,삼성증권     
8                                        하나금융투자     
9                                  유안타증권,신한금융투자     
10                                       한국투자증권     
11                                       DB금융투자     
12                                      IBK투자증권     
13                                       한국투자증권     
14  미래에셋증권,KB증권,현대차증권,한국투자증권,NH투자증권,하나금융투자,삼성증권     
15                                       미래에셋증권     
16                                       한국투자증권     
17                                         신영증권     
18                                       NH투자증권     
19         KB증권,대신증권,신한금융,미래에셋증권,신영증권,하나금융,하이투자     
20                                         대신증권     
21                                         신영증권     
22                                 미래에셋증권,현대차증권     
23                                       DB금융투자     
24                                      IBK투자증권

             종목명             공모주일정    확정공모가            희망공모가      청약경쟁률  \
0           보로노이  2022.03.07~03.08        -    50,000~65,000              
1          모아데이타  2022.02.25~02.26        -    24,000~28,000              
2       SK증권스팩7호  2022.02.22~02.23        -      2,000~2,000              
3             노을  2022.02.21~02.22        -    13,000~17,000              
4           비씨엔씨  2022.02.21~02.22        -     9,000~11,500              
5           풍원정밀  2022.02.17~02.18        -    13,200~15,200              
6            브이씨  2022.02.15~02.16        -    15,000~19,500              
7       스톤브릿지벤처스  2022.02.15~02.16        -     9,000~10,500              
8      하나금융스팩21호  2022.02.15~02.16        -      2,000~2,000              
9           퓨런티어  2022.02.14~02.15        -    11,400~13,700              
10       한국스팩10호  2022.02.10~02.11        -      2,000~2,000              
11      바이오에프디엔씨  2022.02.09~02.10        -    23,000~29,000              
12     IBKS스팩17호  2022.02

종목명             공모주일정   확정공모가            희망공모가      청약경쟁률  \
0       하나금융스팩20호  2021.12.16~12.17   2,000      2,000~2,000   339.28:1   
1         NH스팩22호  2021.12.16~12.17   2,000      2,000~2,000   362.29:1   
2          하이스팩7호  2021.12.09~12.10   2,000      2,000~2,000    93.32:1   
3         교보스팩11호  2021.12.09~12.10   2,000      2,000~2,000      107:1   
4        케이티비네트워크  2021.12.06~12.07   5,800      5,800~7,200   327.26:1   
5              툴젠  2021.12.02~12.03  70,000  100,000~120,000   164.13:1   
6   신한서부티엔디리츠(유가)  2021.11.24~11.26   5,000      5,000~5,000   151.98:1   
7      대신밸런스스팩11호  2021.11.22~11.23   2,000      2,000~2,000   150.83:1   
8   미래에셋글로벌리츠(유가)  2021.11.22~11.24   5,000      5,000~5,000    753.4:1   
9           알비더블유  2021.11.11~11.12  21,400    18,700~21,400  3706.79:1   
10           마인즈랩  2021.11.11~11.12  30,000    26,000~30,000     89.9:1   
11          바이옵트로  2021.11.09~11.10   7,500      7,500~8,500    68.11:1   
12             트윔  2021.11.08~11.09  22,000    17,800~20,400  2266.84:1   
13     NH올원리츠(유가)  2021.11.03~11.05   5,000      5,000~5,000   453.48:1   
14         지오엘리먼트  2021.11.02~11.03  10,000      7,600~8,700  1537.44:1   
15           비트나인  2021.11.01~11.02  11,000      8,700~9,700   589.64:1   
16            디어유  2021.11.01~11.02  26,000    18,000~24,000  1598.15:1   
17         아이티아이즈  2021.11.01~11.02  14,300    12,500~14,300   633.61:1   
18           지니너스  2021.10.27~10.28  20,000    24,700~32,200    162.5:1   
19      카카오페이(유가)  2021.10.25~10.26  90,000    60,000~90,000     29.6:1   
20           피코그램  2021.10.25~10.26  12,500    11,000~12,500  1520.35:1   
21             엔켐  2021.10.21~10.22  42,000    30,000~35,000  1275.69:1   
22            리파인  2021.10.20~10.21  21,000    21,000~24,000     5.95:1   
23     지앤비에스엔지니어링  2021.10.19~10.20  17,400    14,300~17,400  1479.87:1   
24       아이패밀리에스씨  2021.10.18~10.19  25,000    39,000~48,000    20.88:1   

                                      주간사 분석  
0                                  하나금융투자     
1                                  NH투자증권     
2                                  하이투자증권     
3                                    교보증권     
4   한국투자증권,NH투자증권,삼성증권,유진투자증권,하이투자증권,KB증권     
5                                  한국투자증권     
6                    한국투자증권,신한금융투자,하나금융투자     
7                                    대신증권     
8                      미래에셋증권,KB증권,NH투자증권     
9                                  미래에셋증권     
10                          NH투자증권,하나금융투자     
11                                 한국투자증권     
12                                   대신증권     
13                     한국투자증권,NH투자증권,대신증권     
14                                 NH투자증권     
15                                 하나금융투자     
16                                 한국투자증권     
17                                 신한금융투자     
18                            대신증권,NH투자증권     
19                삼성증권,대신증권,한국투자증권,신한금융투자     
20                                IBK투자증권     
21                            대신증권,신한금융투자     
22                                   KB증권     
23                                   삼성증권     
24                                   삼성증권

              종목명             공모주일정    확정공모가            희망공모가      청약경쟁률  \
0            보로노이  2022.03.07~03.08        -    50,000~65,000              
1           모아데이타  2022.02.25~02.26        -    24,000~28,000              
2        SK증권스팩7호  2022.02.22~02.23        -      2,000~2,000              
3              노을  2022.02.21~02.22        -    13,000~17,000              
4            비씨엔씨  2022.02.21~02.22        -     9,000~11,500              
5            풍원정밀  2022.02.17~02.18        -    13,200~15,200              
6             브이씨  2022.02.15~02.16        -    15,000~19,500              
7        스톤브릿지벤처스  2022.02.15~02.16        -     9,000~10,500              
8       하나금융스팩21호  2022.02.15~02.16        -      2,000~2,000              
9            퓨런티어  2022.02.14~02.15        -    11,400~13,700              
10        한국스팩10호  2022.02.10~02.11        -      2,000~2,000              
11       바이오에프디엔씨  2022.02.09~02.10        -    23,000~29,000              
12      IBKS

종목명             공모주일정   확정공모가          희망공모가      청약경쟁률  \
0        차백신연구소  2021.10.12~10.13  11,000  11,000~15,000    42.16:1   
1          지아이텍  2021.10.12~10.13  14,000  11,500~13,100  2968.35:1   
2       NH스팩21호  2021.10.05~10.06   2,000    2,000~2,000   477.64:1   
3       케이카(유가)  2021.09.30~10.01  25,000  34,300~43,200     8.72:1   
4          씨유테크  2021.09.28~09.29   6,000    5,100~5,600  1408.69:1   
5            원준  2021.09.27~09.28  65,000  52,000~60,000  1623.28:1   
6     하나금융스팩19호  2021.09.27~09.28   2,000    2,000~2,000    95.76:1   
7          아스플로  2021.09.27~09.28  25,000  19,000~22,000  2818.08:1   
8       NH스팩20호  2021.09.23~09.24   2,000    2,000~2,000   480.51:1   
9          에스앤디  2021.09.14~09.15  28,000  30,000~32,000     4.20:1   
10         실리콘투  2021.09.14~09.15  27,200  23,800~27,200     1701:1   
11        프롬바이오  2021.09.14~09.15  18,000  21,500~24,500    48.24:1   
12       신한스팩8호  2021.09.13~09.14   2,000    2,000~2,000   361.39:1   
13       바이오플러스  2021.09.13~09.14  31,500  28,500~31,500  1206.63:1   
14    현대중공업(유가)  2021.09.07~09.08  60,000  52,000~60,000   404.29:1   
15   대신밸런스스팩10호  2021.09.06~09.07   2,000    2,000~2,000   207.57:1   
16       유진스팩7호  2021.09.02~09.03   2,000    2,000~2,000  3921.38:1   
17         와이엠텍  2021.08.31~09.01  28,000  21,000~25,000  2939.57:1   
18         에이비온  2021.08.30~08.31  17,000  14,500~17,000    30.66:1   
19     SK리츠(유가)  2021.08.30~09.01   5,000    5,000~5,000      552:1   
20  일진하이솔루스(유가)  2021.08.24~08.25  34,300  25,700~34,300    654.5:1   
21    IBKS스팩16호  2021.08.24~08.25   2,000    2,000~2,000   388.37:1   
22         바이젠셀  2021.08.12~08.13  52,700  42,800~52,700    886.2:1   
23      브레인즈컴퍼니  2021.08.09~08.10  25,000  20,000~22,500  1190.39:1   
24     아주스틸(유가)  2021.08.09~08.10  15,100  12,700~15,100  1419.73:1   

                                        주간사 분석  
0                                      삼성증권     
1                                    미래에셋증권     
2                                    NH투자증권     
3                   NH투자증권,대신증권,삼성증권,하나금융투자     
4                                      대신증권     
5                                    NH투자증권     
6                                    하나금융투자     
7                                    미래에셋증권     
8                                    NH투자증권     
9                                    유진투자증권     
10                              삼성증권,미래에셋증권     
11                                   NH투자증권     
12                                   신한금융투자     
13                                     키움증권     
14  미래에셋,한국투자,하나금융,KB증권,삼성증권,대신증권,DB금융,신영증권     
15                                     대신증권     
16                                     유진증권     
17                                     KB증권     
18                     미래에셋증권,한화투자증권,유진투자증권     
19                  한국투자증권,삼성증권,SK증권,하나금융투자     
20                   미래에셋증권,삼성증권,현대차증권,대신증권     
21                                  IBK투자증권     
22                                대신증권,KB증권     
23                                     키움증권     
24                                   미래에셋증권

...

종목명             공모주일정  확정공모가          희망공모가      청약경쟁률      주간사  \
0           디이엔티  2005.01.17~01.18      4    4,200~5,000      529:1     대우증권   
1   에스엔유프리시젼(유가)  2005.01.12~01.14     27  25,000~29,000   631.18:1     동원증권   
2         인터넷엠비씨  2005.01.11~01.13      3    4,000~4,800   516.03:1     미래에셋   
3             서산  2005.01.11~01.13     12              0  161.5 : 1     미래에셋   
4          인프라밸리  2005.01.10~01.11      8  10,000~12,000      404:1     교보증권   
5         비아이이엠티  2005.01.05~01.06      3    3,700~4,500   455.68:1     대신증권   
6            손오공  2004.12.27~12.29  9,300   9,000~11,000                한양증권   
7         아이크래프트  2004.12.21~12.23      6    6,500~8,000              미래에셋증권   
8          메가스터디  2004.12.08~12.09     18  19,000~23,000   254.03:1  굿모닝신한증권   
9         대주전자재료  2004.12.02~12.03      3    3,200~4,000      120:1     한투증권   
10         모빌리언스  2004.12.01~12.02      4    6,500~8,500       91:1     교보증권   
11          텔레칩스  2004.12.01~12.02      4    5,000~6,000      325:1     대우증권   
12     넥스트인스트루먼트  2004.11.29~11.30      2    3,200~4,100       63:1     교보증권   
13           유니드  2004.11.23~11.24     14  14,200~17,400     95.5:1     삼성증권   
14        화인에이티씨  2004.11.22~11.23      2    2,800~3,200              LG투자증권   
15       토비스(유가)  2004.11.09~11.10      2    2,600~3,300     7.17:1    브릿지증권   
16          한서제약  2004.11.09~11.10      1              0                       
17         케이이엔지  2004.10.20~10.21      2    3,000~4,000                동양증권   
18           모코코  2004.10.20~10.21      2    3,000~3,800                동원증권   
19         신지소프트  2004.10.19~10.20      9   9,000~12,000              미래에셋증권   
20       디지탈디바이스  2004.10.19~10.20      3    3,500~4,500                우리증권   
21          태양기전  2004.10.18~10.19     14  16,000~21,000   241.25:1     교보증권   
22          국일제지  2004.10.12~10.13     15              0      251:1     현대증권   
23          디엠에스  2004.09.15~09.16     28              0      192:1     한화증권   
24          코아로직  2004.08.03~08.04     23  28,000~32,000   0.84 : 1   미래에셋증권   

   분석  
0      
1      
2      
3      
4      
5      
6      
7      
8      
9      
10     
11     
12     
13     
14     
15     
16     
17     
18     
19     
20     
21     
22     
23     
24

           종목명             공모주일정 확정공모가          희망공모가     청약경쟁률  \
0         보로노이  2022.03.07~03.08     -  50,000~65,000             
1        모아데이타  2022.02.25~02.26     -  24,000~28,000             
2     SK증권스팩7호  2022.02.22~02.23     -    2,000~2,000             
3           노을  2022.02.21~02.22     -  13,000~17,000             
4         비씨엔씨  2022.02.21~02.22     -   9,000~11,500             
5         풍원정밀  2022.02.17~02.18     -  13,200~15,200             
6          브이씨  2022.02.15~02.16     -  15,000~19,500             
...        ...               ...   ...            ...       ...   
1343       모코코  2004.10.20~10.21     2    3,000~3,800             
1344     신지소프트  2004.10.19~10.20     9   9,000~12,000             
1345   디지탈디바이스  2004.10.19~10.20     3    3,500~4,500             
1346      태양기전  2004.10.18~10.19    14  16,000~21,000  241.25:1   
1347      국일제지  2004.10.12~10.13    15              0     251:1   
1348      디엠에스  2004.09.15~09.16    28              0     192:

종목명             공모주일정 확정공모가          희망공모가       청약경쟁률   주간사 분석
0        신성델타테크  2004.07.27~07.28     1    1,700~2,200              하나증권   
1     유니퀘스트(유가)  2004.07.22~07.23     4    5,500~6,500              LG증권   
2       한국경제티브이  2004.07.21~07.22    10  10,600~13,000  152.33 : 1  삼성증권   
3     동아에스텍(유가)  2004.07.21~07.22     1    1,800~2,100   23.34 : 1  동원증권   
4  LG필립스엘시디(유가)  2004.07.19~07.20    34  37,100~52,600    7.23 : 1  동원증권   
5            다날  2004.07.13~07.14     8  10,000~12,000   68.25 : 1  LG증권   
6      텔코웨어(유가)  2004.07.08~07.09    12  12,000~15,500   45.72 : 1  삼성증권   
7          아이레보  2003.12.15~12.16     6    5,000~6,500              교보증권   
8           레인콤  2003.12.09~12.10    47  37,000~47,000              현대증권   
9           비트윈  2003.12.09~12.10     4    3,500~4,500              미래에셋

               종목명             공모주일정 확정공모가          희망공모가      청약경쟁률  \
0             보로노이  2022.03.07~03.08     -  50,000~65,000              
1            모아데이타  2022.02.25~02.26     -  24,000~28,000              
2         SK증권스팩7호  2022.02.22~02.23     -    2,000~2,000              
3               노을  2022.02.21~02.22     -  13,000~17,000              
4             비씨엔씨  2022.02.21~02.22     -   9,000~11,500              
5             풍원정밀  2022.02.17~02.18     -  13,200~15,200              
6              브이씨  2022.02.15~02.16     -  15,000~19,500              
...            ...               ...   ...            ...        ...   
1353     동아에스텍(유가)  2004.07.21~07.22     1    1,800~2,100  23.34 : 1   
1354  LG필립스엘시디(유가)  2004.07.19~07.20    34  37,100~52,600   7.23 : 1   
1355            다날  2004.07.13~07.14     8  10,000~12,000  68.25 : 1   
1356      텔코웨어(유가)  2004.07.08~07.09    12  12,000~15,500  45.72 : 1   
1357          아이레보  2003.12.15~12.16     6    5,000~6,500       

Empty DataFrame
Columns: [종목명, 공모주일정, 확정공모가, 희망공모가, 청약경쟁률, 주간사, 분석]
Index: []

In [151]:
#38커뮤니케이션 사이트에서 신규상장 페이지의 데이터 가져오기
tempdata=[]
page=1
all_gongmo_newstock=[]

while(1):
    url = r'http://www.38.co.kr/html/fund/index.htm?o=nw&'

    request=requests.get(url, {'page': str(page)})

    html=request.text

    soup=BeautifulSoup(html, 'html.parser')
    #soup

    #for parse in soup.find_all('table', {'summary':'신규상장종목'}):
    #    print(parse)

    temp=soup.find_all('table', {'summary':'신규상장종목'})



    temp2=parser.make2d(temp[0])
    #print(temp2)

    tempdata=pd.DataFrame(temp2[2:], columns=temp2[0])

    tempdata.rename(columns={'기업명':'종목명'}, inplace=True)
    tempdata
    
    if(len(tempdata)==0 or ( (len(tempdata)==1) and (len(tempdata['종목명'][0])==0) ) ):
        break
        
    if (page==1):
        all_gongmo_newstock=tempdata
    else:
        all_gongmo_newstock=pd.concat([all_gongmo_newstock, tempdata], ignore_index=True)
    
    print(all_gongmo_newstock)
    page+=1

종목명       신규상장일   현재가(원)   전일비(%)   공모가(원) 공모가대비등락률(%)  시초가(원)  \
0             브이씨  2022/02/24        -        %        -          -%       -   
1         한국스팩10호  2022/02/21        -        %        -          -%       -   
2         인카금융서비스  2022/02/16        -        %        -          -%       -   
3     현대엔지니어링(유가)  2022/02/15  107,500    3.37%        -          -%       -   
4           나래나노텍  2022/02/08        -        %   17,500          -%       -   
5             아셈스  2022/02/07        -        %    8,000          -%       -   
6       스코넥엔터테인먼트  2022/02/04   34,500    0.00%   13,000     165.38%       -   
7          이지트로닉스  2022/02/04   41,000    0.00%   22,000      86.36%       -   
8    LG에너지솔루션(유가)  2022/01/27        -        %  300,000          -%       -   
9          애드바이오텍  2022/01/24    5,530   -7.06%    7,000        -21%   6,730   
10           케이옥션  2022/01/24   40,000  -23.08%   20,000        100%  40,000   
11            오토앤  2022/01/20   18,350   29.68%    5,300     246.23%   8,800   
12      디비금융스팩10호  2022/01/20    2,135    0.47%    2,000       6.75%   2,075   
13           래몽래인  2021/12/30   16,100   -8.00%   15,000       7.33%  26,000   
14      하나금융스팩20호  2021/12/27    2,730   -5.21%    2,000       36.5%   2,130   
15        NH스팩22호  2021/12/24    2,100   -0.24%    2,000          5%   2,090   
16         하이스팩7호  2021/12/20    2,095   -0.24%    2,000       4.75%   2,060   
17        교보스팩11호  2021/12/20    2,120   -1.62%    2,000          6%   2,065   
18       케이티비네트워크  2021/12/16    4,240   -3.09%    5,800      -26.9%   6,030   
19  신한서부티엔디리츠(유가)  2021/12/10    4,785   -0.62%    5,000       -4.3%   4,805   

   시초/공모(%) 첫날종가(원)    
0         %      예정    
1         %      예정    
2         %      예정    
3         %      예정    
4         %      예정    
5         %      예정    
6         %      예정    
7         %      예정    
8         %      예정    
9    -3.86%   5,950    
10     100%  52,000    
11   66.04%  11,400    
12    3.75%   2,115    
13   73.33%  24,000    
14     6.5%   2,135    
15     4.5%   2,085    
16       3%   2,085    
17    3.25%   2,095    
18    3.97%   5,350    
19    -3.9%   4,915

              종목명       신규상장일   현재가(원)   전일비(%)   공모가(원) 공모가대비등락률(%)  시초가(원)  \
0             브이씨  2022/02/24        -        %        -          -%       -   
1         한국스팩10호  2022/02/21        -        %        -          -%       -   
2         인카금융서비스  2022/02/16        -        %        -          -%       -   
3     현대엔지니어링(유가)  2022/02/15  107,500    3.37%        -          -%       -   
4           나래나노텍  2022/02/08        -        %   17,500          -%       -   
5             아셈스  2022/02/07        -        %    8,000          -%       -   
6       스코넥엔터테인먼트  2022/02/04   34,500    0.00%   13,000     165.38%       -   
7          이지트로닉스  2022/02/04   41,000    0.00%   22,000      86.36%       -   
8    LG에너지솔루션(유가)  2022/01/27        -        %  300,000          -%       -   
9          애드바이오텍  2022/01/24    5,530   -7.06%    7,000        -21%   6,730   
10           케이옥션  2022/01/24   40,000  -23.08%   20,000        100%  40,000   
11            오토앤  2022/01/20   18,350  

종목명       신규상장일   현재가(원)   전일비(%)  공모가(원) 공모가대비등락률(%)   시초가(원)  \
0              툴젠  2021/12/10   71,000   -4.05%  70,000       1.43%   82,300   
1   미래에셋글로벌리츠(유가)  2021/12/03    5,440   -0.37%   5,000        8.8%    5,310   
2      대신밸런스스팩11호  2021/12/02    2,100    0.00%   2,000          5%    2,060   
3            마인즈랩  2021/11/23   26,550   -6.35%  30,000      -11.5%   29,650   
4           알비더블유  2021/11/22   22,250   -4.51%  21,400       3.97%   42,800   
5           바이옵트로  2021/11/18   10,200   -3.32%   7,500         36%    7,300   
6      NH올원리츠(유가)  2021/11/18    5,080   -0.97%   5,000        1.6%    5,490   
7              트윔  2021/11/17   22,800   -4.40%  22,000       3.64%   44,000   
8          지오엘리먼트  2021/11/11   25,450   -6.43%  10,000      154.5%   20,000   
9          아이티아이즈  2021/11/11   18,700   -6.27%  14,300      30.77%   28,600   
10           비트나인  2021/11/10   15,500   -6.06%  11,000      40.91%   15,250   
11            디어유  2021/11/10   58,900   -8.82%  26,000     126.54%   52,000   
12           지니너스  2021/11/08   12,350    6.01%  20,000     -38.25%   18,000   
13      카카오페이(유가)  2021/11/03  137,500   -6.14%  90,000      52.78%  180,000   
14           피코그램  2021/11/03   16,350  -10.41%  12,500       30.8%   25,000   
15             엔켐  2021/11/01  103,500    0.49%  42,000     146.43%   81,600   
16            리파인  2021/10/29   11,950   -2.45%  21,000      -43.1%   18,900   
17     지앤비에스엔지니어링  2021/10/29   18,600    4.20%  17,400        6.9%   24,000   
18       아이패밀리에스씨  2021/10/28   17,050   -0.87%  25,000      -31.8%   28,650   
19         차백신연구소  2021/10/22    9,210   -7.44%  11,000     -16.27%   11,700   

   시초/공모(%)  첫날종가(원)    
0    17.57%   91,100    
1      6.2%    5,230    
2        3%    2,070    
3    -1.17%   38,000    
4      100%   38,950    
5    -2.67%    6,290    
6      9.8%    5,370    
7      100%   41,100    
8      100%   15,900    
9      100%   20,050    
10   38.64%   11,400    
11     100%   66,500    
12     -10%   13,400    
13     100%  193,000    
14     100%   18,600    
15   94.29%   80,000    
16     -10%   14,300    
17   37.93%   19,200    
18    14.6%   25,400    
19    6.36%   13,000

              종목명       신규상장일   현재가(원)   전일비(%)   공모가(원) 공모가대비등락률(%)   시초가(원)  \
0             브이씨  2022/02/24        -        %        -          -%        -   
1         한국스팩10호  2022/02/21        -        %        -          -%        -   
2         인카금융서비스  2022/02/16        -        %        -          -%        -   
3     현대엔지니어링(유가)  2022/02/15  107,500    3.37%        -          -%        -   
4           나래나노텍  2022/02/08        -        %   17,500          -%        -   
5             아셈스  2022/02/07        -        %    8,000          -%        -   
6       스코넥엔터테인먼트  2022/02/04   34,500    0.00%   13,000     165.38%        -   
7          이지트로닉스  2022/02/04   41,000    0.00%   22,000      86.36%        -   
8    LG에너지솔루션(유가)  2022/01/27        -        %  300,000          -%        -   
9          애드바이오텍  2022/01/24    5,530   -7.06%    7,000        -21%    6,730   
10           케이옥션  2022/01/24   40,000  -23.08%   20,000        100%   40,000   
11            오토앤  2022/01/2

종목명       신규상장일   현재가(원)  전일비(%)  공모가(원) 공모가대비등락률(%)   시초가(원)  \
0         지아이텍  2021/10/21   28,300   2.72%  14,000     102.14%   28,000   
1      NH스팩21호  2021/10/15    2,305   0.00%   2,000      15.25%    2,075   
2      케이카(유가)  2021/10/13   27,450  -5.99%  25,000        9.8%   22,500   
3         씨유테크  2021/10/08    6,590  -6.92%   6,000       9.83%   12,000   
4           원준  2021/10/07  106,700  -6.16%  65,000      64.15%  102,000   
5    하나금융스팩19호  2021/10/07    2,100  -0.47%   2,000          5%    2,045   
6         아스플로  2021/10/07   21,350  -3.83%  25,000      -14.6%   36,000   
7      NH스팩20호  2021/10/05    2,070   0.24%   2,000        3.5%    2,030   
8         에스앤디  2021/09/29   18,300  -1.35%  28,000     -34.64%   25,200   
9         실리콘투  2021/09/29   17,850  -2.99%  27,200     -34.38%   38,500   
10       프롬바이오  2021/09/28    9,950  -7.44%  18,000     -44.72%   19,250   
11      신한스팩8호  2021/09/27    2,100   0.00%   2,000          5%    2,100   
12      바이오플러스  2021/09/27   22,450  -3.85%  31,500     -28.73%   39,500   
13  대신밸런스스팩10호  2021/09/17    2,160   0.23%   2,000          8%    2,305   
14   현대중공업(유가)  2021/09/17   97,700  -3.74%  60,000      62.83%  111,000   
15    SK리츠(유가)  2021/09/14    6,070  -0.33%   5,000       21.4%    5,340   
16      유진스팩7호  2021/09/13    2,120   0.00%   2,000          6%    4,000   
17        와이엠텍  2021/09/10   37,350  -4.23%  28,000      33.39%   56,000   
18        에이비온  2021/09/08   10,700   0.47%  17,000     -37.06%   16,800   
19   IBKS스팩16호  2021/09/03    2,150   0.00%   2,000        7.5%    4,000   

   시초/공모(%)  첫날종가(원)    
0      100%   36,400    
1     3.75%    2,075    
2      -10%   23,000    
3      100%    8,400    
4    56.92%   87,000    
5     2.25%    2,045    
6       44%   28,350    
7      1.5%    2,050    
8      -10%   21,700    
9    41.54%   29,000    
10    6.94%   19,850    
11       5%    2,080    
12    25.4%   32,450    
13   15.25%    2,220    
14      85%  111,500    
15     6.8%    5,780    
16     100%    2,800    
17     100%   59,000    
18   -1.18%   15,700    
19     100%    2,475

...

종목명       신규상장일 현재가(원) 전일비(%)  공모가(원) 공모가대비등락률(%)  시초가(원) 시초/공모(%)  \
0         제이티  2006/10/27      -      %   2,700           %   4,000   48.15%   
1         이녹스  2006/10/20      -      %   6,500           %   9,630   48.15%   
2        광진윈텍  2006/10/20      -      %   2,600           %   5,200     100%   
3    삼정펄프(유가)  2006/10/17      -      %  29,000           %  55,400   91.03%   
4        용현비엠  2006/10/10      -      %   9,000           %  13,000   44.44%   
5          바텍  2006/09/28      -      %   6,700           %   8,920   33.13%   
6   엠디에스테크놀로지  2006/09/26      -      %  13,000           %  17,500   34.62%   
7    현대EP(유가)  2006/09/25      -      %  18,500           %  37,000     100%   
8          평산  2006/08/22      -      %  15,500           %  24,400   57.42%   
9         엘씨텍  2006/08/08      -      %   1,500           %   3,000     100%   
10        지오텔  2006/08/01      -      %   9,800           %   9,250   -5.61%   
11       트라이콤  2006/07/25      -      %   4,800           %   4,320     -10%   
12        젠트로  2006/07/25      -      %   2,200           %   2,400    9.09%   
13       티엘아이  2006/07/25      -      %  11,400           %  11,000   -3.51%   
14       엑스씨이  2006/07/21      -      %   7,500           %   6,900      -8%   
15     한국전자금융  2006/07/14      -      %  20,500           %  32,950   60.73%   
16     미디어플렉스  2006/07/07      -      %  24,000           %  37,500   56.25%   
17    팬엔터테인먼트  2006/07/07      -      %   7,000           %   9,900   41.43%   
18    맥스엔지니어링  2006/07/04      -      %   2,900           %   4,285   47.76%   
19      사이버패스  2006/07/04      -      %   5,200           %   4,860   -6.54%   

   첫날종가(원)    
0    3,400    
1    8,290    
2    5,980    
3   48,500    
4   11,400    
5    9,000    
6   20,100    
7   42,550    
8   21,400    
9    3,450    
10   7,870    
11   3,675    
12   2,760    
13   9,820    
14   6,850    
15  28,050    
16  34,800    
17   8,420    
18   3,645    
19   4,140

              종목명       신규상장일   현재가(원) 전일비(%)  공모가(원) 공모가대비등락률(%)  시초가(원)  \
0             브이씨  2022/02/24        -      %       -          -%       -   
1         한국스팩10호  2022/02/21        -      %       -          -%       -   
2         인카금융서비스  2022/02/16        -      %       -          -%       -   
3     현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%       -   
4           나래나노텍  2022/02/08        -      %  17,500          -%       -   
5             아셈스  2022/02/07        -      %   8,000          -%       -   
6       스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%       -   
...           ...         ...      ...    ...     ...         ...     ...   
1233         티엘아이  2006/07/25        -      %  11,400           %  11,000   
1234         엑스씨이  2006/07/21        -      %   7,500           %   6,900   
1235       한국전자금융  2006/07/14        -      %  20,500           %  32,950   
1236       미디어플렉스  2006/07/07        -      %  24,000           %  37,500   

종목명       신규상장일 현재가(원) 전일비(%) 공모가(원) 공모가대비등락률(%)  시초가(원) 시초/공모(%)  \
0   인포뱅크  2006/07/04      -      %  4,600           %   4,610    0.22%   
1  켐트로닉스  2006/01/17      -      %  9,500           %   9,800    3.16%   
2   오스코텍  2006/01/17      -      %  9,000           %  13,000   44.44%   

  첫날종가(원)    
0   3,920    
1  11,250    
2  14,950

              종목명       신규상장일   현재가(원) 전일비(%)  공모가(원) 공모가대비등락률(%)  시초가(원)  \
0             브이씨  2022/02/24        -      %       -          -%       -   
1         한국스팩10호  2022/02/21        -      %       -          -%       -   
2         인카금융서비스  2022/02/16        -      %       -          -%       -   
3     현대엔지니어링(유가)  2022/02/15  107,500  3.37%       -          -%       -   
4           나래나노텍  2022/02/08        -      %  17,500          -%       -   
5             아셈스  2022/02/07        -      %   8,000          -%       -   
6       스코넥엔터테인먼트  2022/02/04   34,500  0.00%  13,000     165.38%       -   
...           ...         ...      ...    ...     ...         ...     ...   
1236       미디어플렉스  2006/07/07        -      %  24,000           %  37,500   
1237      팬엔터테인먼트  2006/07/07        -      %   7,000           %   9,900   
1238      맥스엔지니어링  2006/07/04        -      %   2,900           %   4,285   
1239        사이버패스  2006/07/04        -      %   5,200           %   4,860   

Empty DataFrame
Columns: [종목명, 신규상장일, 현재가(원), 전일비(%), 공모가(원), 공모가대비등락률(%), 시초가(원), 시초/공모(%), 첫날종가(원), ]
Index: []